In [ ]:
# 📌 Install required packages
!pip install telethon nest_asyncio

import os
import json
import time
import requests
import subprocess
import asyncio
import nest_asyncio
from datetime import datetime
from telethon import TelegramClient

# ✅ Fix for Colab's asyncio issue
nest_asyncio.apply()

# 🔹 Telegram API credentials (Replace with actual values)
API_ID = 4874239
API_HASH = "de7cc0ec7a9e4312ddc2eed4062be667"
BOT_TOKEN = "7688645716:AAElhspRAcmQY-HVJfaRXHrMcRo78EZA770"
CHANNEL_ID = -1002385619119  # Private channel ID

# 🔹 JSON URL for fetching image & audio
JSON_URL = "https://amar.eu.org/TelegramBOT/redirect_urls.json"

# 🔹 Paths for downloaded files
IMAGE_PATH = "/content/image.jpg"
AUDIO_PATH = "/content/audio.mp3"
VIDEO_PATH = f"/content/audiobook_{datetime.now().strftime('%Y-%m-%d_%H-%M')}.mp4"

# ✅ Step 1: Download Image & Audio
print("⬇️ Downloading image and audio...")

response = requests.get(JSON_URL)
if response.status_code == 200:
    data = response.json()
    image_url = data.get("image")
    audio_url = data.get("audio")

    if image_url and audio_url:
        # Download image
        img_response = requests.get(image_url)
        with open(IMAGE_PATH, "wb") as img_file:
            img_file.write(img_response.content)
        print(f"⬇️ Downloaded: {IMAGE_PATH}")

        # Download audio
        audio_response = requests.get(audio_url)
        with open(AUDIO_PATH, "wb") as audio_file:
            audio_file.write(audio_response.content)
        print(f"⬇️ Downloaded: {AUDIO_PATH}")

    else:
        print("❌ Invalid JSON data!")
        exit()
else:
    print("❌ Failed to fetch JSON data!")
    exit()

# ✅ Step 2: Get Audio Duration
def get_audio_duration(audio_path):
    print("⏳ Getting audio duration...")
    try:
        command = [
            "ffprobe", "-v", "quiet", "-print_format", "json",
            "-show_format", "-i", audio_path
        ]
        result = subprocess.run(command, stdout=subprocess.PIPE, stderr=subprocess.PIPE, text=True)
        if result.returncode == 0:
            duration = float(json.loads(result.stdout)["format"]["duration"])
            return duration
    except Exception as e:
        print(f"❌ Error getting duration: {e}")
    return None

duration = get_audio_duration(AUDIO_PATH)
if not duration:
    print("❌ Failed to get audio duration!")
    exit()

# ✅ Step 3: Create Video with FFmpeg
print("🎥 Creating video...")
def create_video(image, audio, output, duration):
    print("🎬 Video Processing Started...")

    command = [
        "ffmpeg", "-y", "-loop", "1", "-i", image, "-i", audio,
        "-c:v", "h264_nvenc", "-c:a", "aac", "-b:v", "1000k", "-preset", "fast",
        "-t", str(duration), "-r", "30",
        "-vf", "scale=1280:720:force_original_aspect_ratio=decrease,pad=1280:720:(ow-iw)/2:(oh-ih)/2",
        "-pix_fmt", "yuv420p", output
    ]

    process = subprocess.Popen(command, stdout=subprocess.PIPE, stderr=subprocess.PIPE, text=True)

    while True:
        output_line = process.stderr.readline()
        if not output_line and process.poll() is not None:
            break

        if "time=" in output_line:
            parts = output_line.strip().split("time=")[-1].split(" ")[0].split(":")
            if len(parts) == 3:
                h, m, s = map(float, parts)
                current_time = h * 3600 + m * 60 + s
                percentage = min(100, (current_time / duration) * 100)
                print(f"\r📽️ Video Processing: {percentage:.2f}% completed", end="")

    print("\n✅ Video creation successful!")

start_time = time.time()
create_video(IMAGE_PATH, AUDIO_PATH, VIDEO_PATH, duration)
end_time = time.time()
print(f"⏳ Video creation took: {end_time - start_time:.2f} seconds")

# ✅ Step 4: Upload Video to Telegram
async def send_video():
    print("📤 Uploading video to Telegram...")
    client = TelegramClient("uploader", API_ID, API_HASH)

    await client.start(bot_token=BOT_TOKEN)  # ✅ Corrected way to start the client

    try:
        await client.send_file(CHANNEL_ID, VIDEO_PATH, caption="📚 New Audiobook Available!")
        print("✅ Video uploaded successfully!")
    except Exception as e:
        print(f"❌ Telegram Upload Error: {e}")
    finally:
        await client.disconnect()

# 🔹 Run the async function properly in Colab
loop = asyncio.get_event_loop()
loop.run_until_complete(send_video())

print("🎉 Task completed!")